# Exercise 8: Sound transformations

In this exercise you will use the HPS model to creatively transform sounds. There are two parts in this exercise. In the first one you should perform a natural sounding transformation on the speech sound that you used in the previous exercise (E7). In the second part you should select a sound of your choice and do a "creative" transformation. You will have to write a short description of the sound and of the transformation you did, giving the link to the original sound and uploading several transformed sounds.

For this exercise, you can use the `transformations_GUI.py` (in `software/transformations_interface/`) to try things, once decided you can fill up the code in this file. You can also do everything from here and add any new code you wish.

In order to perform a good/interesting transformation you should make sure that you have performed an analysis that is adequate for the type of transformation you want to do. Not every HPS analysis representation will work for every type of sound transformation. There will be things in the analysis that when modified will result in undesired artifacts. In general, for any transformation, it is best to have the harmonic values as smooth and continuous as possible and an stochastic representation as smooth and with as few values as possible. It might be much better to start with an analysis representation that does not result in the best reconstruction in exchange of having smoother and more compact data.

To help you with the exercise, we give a brief description of the transformation parameters used by the HPS transformation function:

1. `freqScaling`: frequency scaling factors to be applied to the harmonics of the sound, in time-value pairs (where value of 1 is no scaling). The time values can be normalized, from 0 to 1, or can correspond to the times in seconds of the input sound. The scaling factor is a multiplicative factor, thus a value of 1 is no change. Example: to transpose an octave the sound you can specify `[0, 2, 1, 2]`.
2. `freqStretching`: frequency stretching factors to be applied to the harmonics of the sound, in time-value pairs (value of 1 is no stretching). The time values can be normalized, from 0 to 1, or can correspond to the times in seconds of the input sound. The stretching factor is a multiplicative factor whose effect depend on the harmonic number, higher harmonics being more affected that lower ones, thus resulting in an inharmonic effect. A value of 1 results in no transformation. Example: an array like `[0, 1.2, 1, 1.2]` will result in a perceptually large inharmonic effect.
3. `timbrePreservation`: 1 preserves the original timbre, 0 does not. It can only have a value of 0 or of 1. By setting the value to 1 the spectral shape of the original sound is preserved even when the frequencies of the sound are modified. In the case of speech it would correspond to the idea of preserving the identity of the speaker after the transformation.
4. `timeScaling`: time scaling factors to be applied to the whole sound, in time-value pairs (value of 1 is no scaling). The time values can be normalized, from 0 to 1, or can correspond to the times in seconds of the input sound. The time scaling factor is a multiplicative factor, thus 1 is no change. Example: to stretch the original sound to twice the original duration, we can specify `[0, 0, 1, 2]`.

All the transformation values can have as many points as desired, but they have to be in the form of an array with time-value pairs, so of even size. For example a good array for a frequency stretching of a sound that has a duration of 3.146 seconds could be: `[0, 1.2, 2.01, 1.2, 2.679, 0.7, 3.146, 0.7]`.

## Part 1. Perform natural sounding transformations of a speech sound

Use the HPS model with the sound `speech-female.wav`, available in the sounds directory, to first analyze and then obtain a natural sounding transformation of the sound. The synthesized sound should sound as different as possible to the original sound while sounding natural. By natural we mean that it should sound like speech, that it could have been possible to be produced by a human, and by listening we should consider it as a speech sound, even though we might not be able to understand it. You should first make sure that you start from a good analysis, then you can do time and/or frequency scaling transformations. The transformation should be done with a single pass, no mixing of sounds coming from different transformations. Since you used the same sound in A7, use that experience to get a good analysis, but consider that the analysis, given that we now want to use it for applying a very strong transformation, might be done differently than what you did in A7.

Write a short paragraph for every transformation, explaining what you wanted to obtain and explaining the transformations you did, giving both the analysis and transformation parameter values (sufficiently detailed for the evaluator to be able to reproduce the analysis and transformation).

In [1]:
import numpy as np
import matplotlib.pyplot as plt
from scipy.signal import get_window
import sys, os
sys.path.append('../software/models/')
sys.path.append('../software/transformations/')
import utilFunctions as UF
import stft as STFT
import hpsModel as HPS
import hpsTransformations as HPST
import harmonicTransformations as HT
import IPython.display as ipd

In [14]:
# 1.1 perform an analysis/synthesis using the HPS model

input_file = '../sounds/speech-female.wav'

### set the parameters
window ='blackman'
M = 2048
N = 2048
t = -100
minSineDur = 0.1
nH = 30
minf0 = 100
maxf0 = 250
f0et = 5.0
harmDevSlope = 0.01
stocf = .5

# no need to modify anything after this
Ns = 512
H = 128

(fs, x) = UF.wavread(input_file)
w = get_window(window, M, fftbins=True)
hfreq, hmag, hphase, stocEnv = HPS.hpsModelAnal(x, fs, w, N, H, t, nH, minf0, maxf0, f0et, harmDevSlope, minSineDur, Ns, stocf)
y, yh, yst = HPS.hpsModelSynth(hfreq, hmag, hphase, stocEnv, Ns, H, fs)

print("original sound:")
ipd.display(ipd.Audio(data=x, rate=fs))
print("HPS:")
ipd.display(ipd.Audio(data=y, rate=fs))
print("residual:")
ipd.display(ipd.Audio(data=yst, rate=fs))

### explain your parameter choices

print("Explenation: I took the parameters I used in the last excercise and used them as a start point. I lowered down the threshold and i changed the f0et to 5.0 instead of 7.0. Everything else sounded right to me so i left it like that") 

original sound:


HPS:


residual:


Explenation: I took the parameters I used in the last excercise and used them as a start point. I lowered down the threshold and i changed the f0et to 5.0 instead of 7.0. Everything else sounded right to me so i left it like that


In [19]:
# 1.2 Perform a transformation from the previous analysis
#Test 1
### define the transformations
freqScaling = np.array([0,1, 1.25,4, 1.8,1, 2.25,4])
freqStretching = np.array([0,3, 1.25,1])
timbrePreservation = 1
timeScaling = np.array([0,0, 2.25,2.25, 2.5,3.146])


# no need to modify the following code 
Ns = 512
H = 128

# frequency scaling of the harmonics 
hfreqt, hmagt = HT.harmonicFreqScaling(hfreq, hmag, freqScaling, freqStretching, timbrePreservation, fs)

# time scaling the sound
yhfreq, yhmag, ystocEnv = HPST.hpsTimeScale(hfreqt, hmagt, stocEnv, timeScaling)

# synthesis from the trasformed hps representation 
y, yh, yst = HPS.hpsModelSynth(yhfreq, yhmag, np.array([]), ystocEnv, Ns, H, fs)
print("Test 1 :")
### explain your transformations
print("This was my first attempt. Its stretching in the begining, and then it slows down a little bit. I feel like it also makes it sound with a different mood, more like a question type.")
ipd.display(ipd.Audio(data=y, rate=fs))


#Test 2
freqScaling = np.array([0,0.25])
freqStretching = np.array([0,1])
timbrePreservation = 1
timeScaling = np.array([ 0,0, 6,3.146])
Ns = 512
H = 128
hfreqt, hmagt = HT.harmonicFreqScaling(hfreq, hmag, freqScaling, freqStretching, timbrePreservation, fs)
yhfreq, yhmag, ystocEnv = HPST.hpsTimeScale(hfreqt, hmagt, stocEnv, timeScaling) 
y, yh, yst = HPS.hpsModelSynth(yhfreq, yhmag, np.array([]), ystocEnv, Ns, H, fs)
print("Test 2 :")
print("This was my second attempt, honestly i tried to play more and see what happened, thought i would make it sound slower but it was the opposite and it made it faster. It ended up sounding like its coming from a star wars or star trek movie")
ipd.display(ipd.Audio(data=y, rate=fs))


#Test 3
freqScaling = np.array([0,0.25])
freqStretching = np.array([0,1])
timbrePreservation = 1
timeScaling = np.array([0,0, 1,3.146])
Ns = 512
H = 128
hfreqt, hmagt = HT.harmonicFreqScaling(hfreq, hmag, freqScaling, freqStretching, timbrePreservation, fs)
yhfreq, yhmag, ystocEnv = HPST.hpsTimeScale(hfreqt, hmagt, stocEnv, timeScaling) 
y, yh, yst = HPS.hpsModelSynth(yhfreq, yhmag, np.array([]), ystocEnv, Ns, H, fs)

print("Test 3 :")
print("This was my last attempt. I did manage to make things slower and now it sounds like its possessed by a demon or something like that. I liked the result at the end")
ipd.display(ipd.Audio(data=y, rate=fs))

Test 1 :
This was my first attempt. Its stretching in the begining, and then it slows down a little bit. I feel like it also makes it sound with a different mood, more like a question type.


Test 2 :
This was my second attempt, honestly i tried to play more and see what happened, thought i would make it sound slower but it was the opposite and it made it faster. It ended up sounding like its coming from a star wars or star trek movie


Test 3 :
This was my last attempt. I did manage to make things slower and now it sounds like its possessed by a demon or something like that. I liked the result at the end


## Part 2. Perform creative transformations with a sound of your choice

Pick any natural and harmonic sound from Freesound and use the HPS model to do the most creative and interesting transformation you can come up with. Sounding as different as possible from the original sound.

It is essential that you start with a natural harmonic sound. Examples include (but not limited to) any acoustic harmonic instrument, speech, harmonic sound from nature, etc. As long as they have a harmonic structure, you can use it. You can even reuse the sound you used in A7-Part2 or upload your own sound to freesound and then use it.

The sound from Freesound to use could be in any format, but to use the sms-tools software you will have to first convert it to be a monophonic file (one channel), sampling rate of 44100, and 16bits samples.

You can do any interesting transformation with a single pass. It is not allowed to mix sounds obtained from different transformations. The transformed sound need not sound natural. So, time to show some creativity!

Write a short paragraph for every transformation, explaining what you wanted to obtain and explaining the transformations you did, giving both the analysis and transformation parameter values (sufficiently detailed for the evaluator to be able to reproduce the analysis and transformation).

In [20]:
# 1.1 perform an analysis/synthesis using the HPS model

### set the parameters
input_file = '../sounds/trombone.wav'
window ='blackman'
M = 2001
N = 2048
t = -80
minSineDur = 0.1
nH = 20
minf0 = 100
maxf0 = 400
f0et = 5.0
harmDevSlope = 0.01
stocf = .2

# no need to modify anything after this
Ns = 512
H = 128

(fs, x) = UF.wavread(input_file)
w = get_window(window, M, fftbins=True)
hfreq, hmag, hphase, stocEnv = HPS.hpsModelAnal(x, fs, w, N, H, t, nH, minf0, maxf0, f0et, harmDevSlope, minSineDur, Ns, stocf)
y, yh, yst = HPS.hpsModelSynth(hfreq, hmag, hphase, stocEnv, Ns, H, fs)

print("Trombone:")
ipd.display(ipd.Audio(data=x, rate=fs))
print("HPS:")
ipd.display(ipd.Audio(data=y, rate=fs))
print("Residual:")
ipd.display(ipd.Audio(data=yst, rate=fs))
print("harmonics:")
ipd.display(ipd.Audio(data=yh, rate=fs))

### explain your parameter choices
print("I chose a trombone playing a long E#3 note. I think the foundamental frequency is between 150 and 250 so I chose an M of 2001, which gave me an N of 2048. I also chose the min frequency to be 100 and the maximum to be 400 so i could get the foundamental.")
print("https://freesound.org/people/Samulis/sounds/374031/")


Trombone:


HPS:


Residual:


harmonics:


I chose a trombone playing a long E#3 note. I think the foundamental frequency is between 150 and 250 so I chose an M of 2001, which gave me an N of 2048. I also chose the min frequency to be 100 and the maximum to be 400 so i could get the foundamental.
https://freesound.org/people/Samulis/sounds/374031/


In [23]:
# 1.2 Perform a transformation from the previous analysis
#Test 1
### define the transformations
freqScaling = np.array([0,1, 1,4, 2,8, 3,3, 4,0.1, 5,1])
freqStretching = np.array([0,1, 4,1.3])
timbrePreservation = 1
timeScaling = np.array([0,0, 2,3, 3,4, 6,5])


# no need to modify anything after this
Ns = 512
H = 128

# frequency scaling of the harmonics 
hfreqt, hmagt = HT.harmonicFreqScaling(hfreq, hmag, freqScaling, freqStretching, timbrePreservation, fs)

# time scaling the sound
yhfreq, yhmag, ystocEnv = HPST.hpsTimeScale(hfreqt, hmagt, stocEnv, timeScaling)

# synthesis from the trasformed hps representation 
y, yh, yst = HPS.hpsModelSynth(yhfreq, yhmag, np.array([]), ystocEnv, Ns, H, fs)

ipd.display(ipd.Audio(data=y, rate=fs))

### explain your transformations
print("This first transformation sounds sci-fi like, once again something coming from star wars haha")

#Test 2
freqScaling = np.array([0,0.0008])
freqStretching = np.array([0,1.5, 10,1.5])
timbrePreservation = 1
timeScaling = np.array([0,0,1,3])
Ns = 512
H = 128
hfreqt, hmagt = HT.harmonicFreqScaling(hfreq, hmag, freqScaling, freqStretching, timbrePreservation, fs)
yhfreq, yhmag, ystocEnv = HPST.hpsTimeScale(hfreqt, hmagt, stocEnv, timeScaling)
y, yh, yst = HPS.hpsModelSynth(yhfreq, yhmag, np.array([]), ystocEnv, Ns, H, fs)

ipd.display(ipd.Audio(data=y, rate=fs))
print("Its pretty simple, just dropped the pitch and slowered it down a little, while writing the explenation I think it might be even way too long haha. Something I did notice is that it sounds with a lot of background noise and some other higher harmonics appeared?")
print("I found this transforming excercises really cool, I think these type of transformations could work really well for some post-production stuff.(Maybe without the background noise)") 

This first transformation sounds sci-fi like, once again something coming from star wars haha


Its pretty simple, just dropped the pitch and slowered it down a little, while writing the explenation I think it might be even way too long haha. Something I did notice is that it sounds with a lot of background noise and some other higher harmonics appeared?
I found this transforming excercises really cool, I think these type of transformations could work really well for some post-production stuff.(Maybe without the background noise)
